# Meteorcruise vs. FOCI NEMO Test data

_**ATTENTION:** This will load > 5G from the internet, store it on Disk, and consume O(50GB) of memory when running. SO make sure you're fine with this kind of resource use before hitting "Run all cells"._

## Description

We use an [Intake driver](https://github.com/ESM-VFC/intake_pangaeapy) for [`pangaeapy`](https://github.com/pangaea-data-publisher/pangaeapy) to load hydrographic observational data from Meteor cruises M85/1, M85/2, M90, M105, M120 and
- plot positions on a map
- create a [temperature-salinity diagram](https://en.wikipedia.org/wiki/Temperature%E2%80%93salinity_diagram) of all cruises.

We load a NEMO test dataset that covers the same time on the calendar and
- plot surface temperature on a map together with the observed temperature
- select data for the same locations and time stamps as in the observational data set and repeate the temperature-salinity diagrams
 
Along the way, there's a few obstacles:
- Selecting NEMO data on a curvilinear horizontal grid is not directly implemented in xarray, so we use [`xorca_lonlat2ij`](git.geomar.de/python/xorca_lonlat2ij) to find closest indices on the sphere.
- We need to un-elegantly mask the data using the fact that over land, the values never change from an exact `0`, because the mask info is in a different file (the mesh-mask) than the actual data.

_**Note** that we cannot expect a lot of similarity between the in-sity observational data and a free running climate model._

## Parameters

In [1]:
# parameters

esm_vfc_data_dir = "../esm-vfc-data/"
nemo_catalog_url = "https://raw.githubusercontent.com/ESM-VFC/esm-vfc-catalogs/master/catalogs/NEMO_ORCA05_FOCI_Test_Full.yaml"
meteor_catalog_url = "https://raw.githubusercontent.com/ESM-VFC/esm-vfc-catalogs/master/catalogs/METEOR_cruises.yaml"
host = !hostname
host = host[0]
dask_cluster_args = dict(n_workers=4, threads_per_worker=2, memory_limit=12e9, host=host)

## Tech preamble

In [2]:
import numpy as np
import pandas as pd
import xarray as xr

In [3]:
# set up intake catalog
import intake
from esmvfc_cattools import fetch_zenodo_data
import os

os.environ["ESM_VFC_DATA_DIR"] = esm_vfc_data_dir

In [4]:
# set up plotting
import hvplot.pandas
import hvplot.xarray
import geoviews.feature as gf
from holoviews.operation import decimate
from cartopy import crs

In [5]:
# %pip install git+https://git.geomar.de/python/xorca_lonlat2ij.git@v1.0.0
import xorca_lonlat2ij as xll2ij

In [6]:
# set up Dask cluster
from dask.distributed import Client
client = Client(**dask_cluster_args)
client

<Client: 'tcp://10.241.201.2:41940' processes=4 threads=8, memory=48.00 GB>

## Get obs data, extract near-surface measurements, plot positions

In [7]:
meteor_catalog = intake.open_catalog(meteor_catalog_url)
list(meteor_catalog)

['M85_1_bottles',
 'M85_2_bottles',
 'M106_bottles',
 'M120_bottles',
 'M90_bottles']

In [8]:
# OPTIMIZE: Here we could go for dask dataframes partitioned across the cruises.
obs_df = pd.concat(
    (
        meteor_catalog["M85_1_bottles"].read(),
        meteor_catalog["M85_2_bottles"].read(),
        meteor_catalog["M90_bottles"].read(),
        meteor_catalog["M106_bottles"].read(),
        meteor_catalog["M120_bottles"].read()
    ),
    ignore_index=True
)

In [9]:
# Construct and "Event" column that contains the profile number.
# We need to account for the fact that some cruises already have merged
# station and profile events, however.
obs_df["Event"] = obs_df["Event"].where(
    obs_df["Profile"].isnull(),
    obs_df["Event"] + "-" + obs_df["Profile"].fillna("-99").astype(int).astype(str)
)
obs_df = obs_df.drop(columns=["Profile"])

In [10]:
obs_df

Event           Date/Time  Latitude  Longitude  Elevation  \
0       M85/1_693-1 2011-06-25 15:16:00   49.1423   -11.2813     -344.0   
1       M85/1_693-1 2011-06-25 15:16:00   49.1423   -11.2813     -344.0   
2       M85/1_693-1 2011-06-25 15:16:00   49.1423   -11.2813     -344.0   
3       M85/1_693-1 2011-06-25 15:16:00   49.1423   -11.2813     -344.0   
4       M85/1_693-1 2011-06-25 15:16:00   49.1423   -11.2813     -344.0   
...             ...                 ...       ...        ...        ...   
798439  M120_1149-1 2015-11-17 06:47:00  -22.9995    13.5915        NaN   
798440  M120_1149-1 2015-11-17 06:47:00  -22.9995    13.5915        NaN   
798441  M120_1149-1 2015-11-17 06:47:00  -22.9995    13.5915        NaN   
798442  M120_1149-1 2015-11-17 06:47:00  -22.9995    13.5915        NaN   
798443  M120_1149-1 2015-11-17 06:47:00  -22.9995    13.5915        NaN   

        Depth water  Press     Temp     Tpot      Sal  ...  OXYGEN_2  CFC-11  \
0            332.07  335.3  11.0043  10.9624  35.5657  ...     246.5     NaN   
1            331.98  335.2  11.0038  10.9619  35.5659  ...     246.5   3.017   
2            332.17  335.4  11.0041  10.9622  35.5654  ...     246.7     NaN   
3            332.47  335.7  11.0038  10.9619  35.5659  ...     246.8     NaN   
4            332.27  335.5  11.0039  10.9620  35.5654  ...     246.7     NaN   
...             ...    ...      ...      ...      ...  ...       ...     ...   
798439       138.08  139.0  12.2349      NaN  35.1369  ...       NaN     NaN   
798440       139.07  140.0  12.2363      NaN  35.1371  ...       NaN     NaN   
798441       140.06  141.0  12.2300      NaN  35.1366  ...       NaN     NaN   
798442       141.06  142.0  12.2281      NaN  35.1364  ...       NaN     NaN   
798443       142.05  143.0  12.2285      NaN  35.1364  ...       NaN     NaN   

        CFC-12  Bottle       SV  Fluorescence  Turbidity  SPAR    PAR  \
0          NaN     1.0      NaN           NaN        NaN   NaN    NaN   
1       1.7679     2.0      NaN           NaN        NaN   NaN    NaN   
2          NaN     3.0      NaN           NaN        NaN   NaN    NaN   
3          NaN     4.0      NaN           NaN        NaN   NaN    NaN   
4          NaN     5.0      NaN           NaN        NaN   NaN    NaN   
...        ...     ...      ...           ...        ...   ...    ...   
798439     NaN     NaN  1500.08         0.616      0.129   NaN  10.16   
798440     NaN     NaN  1500.10         1.299      0.182   NaN  10.10   
798441     NaN     NaN  1500.10         0.551      0.203   NaN  10.09   
798442     NaN     NaN  1500.11         0.465      0.140   NaN  10.08   
798443     NaN     NaN  1500.13         0.460      0.142   NaN  10.11   

        Sigma in situ  
0                 NaN  
1                 NaN  
2                 NaN  
3                 NaN  
4                 NaN  
...               ...  
798439        26.6538  
798440        26.6537  
798441        26.6545  
798442        26.6547  
798443        26.6547  

[798444 rows x 22 columns]

In [11]:
# restrict to measurements at minimal depth per Event (= station)
near_surface_obs = obs_df.loc[
    obs_df.groupby("Event")["Depth water"].idxmin()
]
near_surface_obs = near_surface_obs.set_index("Event")
near_surface_obs

Date/Time   Latitude  Longitude  Elevation  Depth water  \
Event                                                                          
M106_322-2 2014-04-19 22:42:00  17.600700 -24.249800        NaN         4.97   
M106_322-3 2014-04-20 02:48:00  17.599800 -24.250000        NaN         4.97   
M106_322-5 2014-04-20 05:37:00  17.600000 -24.250300        NaN         3.98   
M106_326-1 2014-04-21 21:33:00  15.000300 -23.001800        NaN         4.97   
M106_326-3 2014-04-21 23:21:00  15.007200 -23.002800        NaN         3.98   
...                        ...        ...        ...        ...          ...   
M90_1707-1 2012-11-26 18:10:00 -15.666467 -76.100617        NaN         4.97   
M90_1708-1 2012-11-26 19:47:00 -15.500183 -76.000433        NaN         2.98   
M90_1709-1 2012-11-26 21:45:00 -15.333683 -75.900217        NaN         2.98   
M90_1710-1 2012-11-26 23:41:00 -15.166200 -75.800067        NaN         1.99   
M90_1711-1 2012-11-27 01:36:00 -14.999967 -75.700117        NaN         3.98   

            Press     Temp  Tpot      Sal  Sigma-theta  ...  OXYGEN_2  CFC-11  \
Event                                                   ...                     
M106_322-2    5.0  22.2999   NaN  36.4072          NaN  ...       NaN     NaN   
M106_322-3    5.0  22.2443   NaN  36.4011          NaN  ...       NaN     NaN   
M106_322-5    4.0  22.2282   NaN  36.3955          NaN  ...       NaN     NaN   
M106_326-1    5.0  23.0284   NaN  35.9497          NaN  ...       NaN     NaN   
M106_326-3    4.0  23.0132   NaN  35.9515          NaN  ...       NaN     NaN   
...           ...      ...   ...      ...          ...  ...       ...     ...   
M90_1707-1    5.0  18.4990   NaN  35.2035          NaN  ...       NaN     NaN   
M90_1708-1    3.0  17.8874   NaN  35.1545          NaN  ...       NaN     NaN   
M90_1709-1    3.0  18.5181   NaN  34.9928          NaN  ...       NaN     NaN   
M90_1710-1    2.0  17.7762   NaN  34.9728          NaN  ...       NaN     NaN   
M90_1711-1    4.0  16.0407   NaN  34.9156          NaN  ...       NaN     NaN   

            CFC-12  Bottle       SV  Fluorescence  Turbidity  SPAR    PAR  \
Event                                                                       
M106_322-2     NaN     NaN  1529.28         0.091      0.242   NaN   0.00   
M106_322-3     NaN     NaN  1529.13         0.087      0.255   NaN   0.00   
M106_322-5     NaN     NaN  1529.06         0.085      0.241   NaN   0.00   
M106_326-1     NaN     NaN  1530.64         0.317      0.196   0.0   0.00   
M106_326-3     NaN     NaN  1530.59         0.306      0.244   0.0   0.00   
...            ...     ...      ...           ...        ...   ...    ...   
M90_1707-1     NaN     NaN      NaN         0.304        NaN   NaN  29.96   
M90_1708-1     NaN     NaN      NaN         1.723        NaN   NaN  25.85   
M90_1709-1     NaN     NaN      NaN         3.955        NaN   NaN  14.23   
M90_1710-1     NaN     NaN      NaN         7.528        NaN   NaN   0.19   
M90_1711-1     NaN     NaN      NaN         3.316        NaN   NaN   0.19   

            Sigma in situ  
Event                      
M106_322-2        25.2028  
M106_322-3        25.2140  
M106_322-5        25.2143  
M106_326-1        24.6461  
M106_326-3        24.6519  
...                   ...  
M90_1707-1            NaN  
M90_1708-1            NaN  
M90_1709-1            NaN  
M90_1710-1            NaN  
M90_1711-1            NaN  

[606 rows x 21 columns]

In [12]:
(
    near_surface_obs.hvplot(
        "Longitude", "Latitude", geo=True, kind="points")
    * gf.coastline
)

:Overlay
   .Points.I    :Points   [Longitude,Latitude]
   .Coastline.I :Feature   [Longitude,Latitude]

_**FIXME:** Hover tool shows wrong values ("Latitude: 7945355th"???)._

In [13]:
len(obs_df), len(near_surface_obs)

(798444, 606)

In [14]:
(
    decimate(obs_df.hvplot.scatter("Temp", "Sal", alpha=0.2, label="all data"), max_samples=2_000)
    * decimate(
        near_surface_obs.hvplot.scatter("Temp", "Sal", alpha=0.8, label="surface data"),
        max_samples=int(2_000 * len(near_surface_obs)**0.5 / len(obs_df)**0.5)  # same thinning as other set of points
    )
)

:DynamicMap   []
   :Overlay
      .Scatter.All_data     :Scatter   [Temp]   (Sal)
      .Scatter.Surface_data :Scatter   [Temp]   (Sal)

## Load catalog and fetch data

In [15]:
model_data_cat = intake.open_catalog(nemo_catalog_url)
fetch_zenodo_data(
    model_data_cat["NEMO_ORCA05_FOCI_Test_grid_T"]
)
fetch_zenodo_data(
    model_data_cat["NEMO_ORCA05_FOCI_Test_mesh_mask"]
)

No need to download ../esm-vfc-data/NEMO_ORCA05_FOCI_Test_Full/FOCI1.14-TEST.2020.04.1_1m_20110101_20111231_grid_T.nc
No need to download ../esm-vfc-data/NEMO_ORCA05_FOCI_Test_Full/FOCI1.14-TEST.2020.04.1_1m_20120101_20121231_grid_T.nc
No need to download ../esm-vfc-data/NEMO_ORCA05_FOCI_Test_Full/FOCI1.14-TEST.2020.04.1_1m_20130101_20131231_grid_T.nc
No need to download ../esm-vfc-data/NEMO_ORCA05_FOCI_Test_Full/FOCI1.14-TEST.2020.04.1_1m_20140101_20141231_grid_T.nc
No need to download ../esm-vfc-data/NEMO_ORCA05_FOCI_Test_Full/FOCI1.14-TEST.2020.04.1_1m_20150101_20151231_grid_T.nc
No need to download ../esm-vfc-data/NEMO_ORCA05_FOCI_Test_Full/FOCI1.14-TEST.2020.04.1_1m_20160101_20161231_grid_T.nc
No need to download ../esm-vfc-data/NEMO_ORCA05_FOCI_Test_Full/FOCI1.14-TEST.2020.04.1_1m_20170101_20171231_grid_T.nc
No need to download ../esm-vfc-data/NEMO_ORCA05_FOCI_Test_Full/FOCI1.14-TEST.2020.04.1_1m_20180101_20181231_grid_T.nc
No need to download ../esm-vfc-data/NEMO_ORCA05_FOCI_Tes

## Restrict to North Atlantic, calc mean SST, plot with obs positions

In [16]:
# hydrographic data
model_dataset = model_data_cat["NEMO_ORCA05_FOCI_Test_grid_T"](
    chunks={"time_counter": 1, "deptht": 23}
).to_dask()
model_dataset = model_dataset.set_coords(["nav_lat", "nav_lon"])
model_dataset["nav_lat"] = model_dataset["nav_lat"].isel(time_counter=0).squeeze()
model_dataset["nav_lon"] = model_dataset["nav_lon"].isel(time_counter=0).squeeze()
model_dataset = xr.decode_cf(model_dataset)

# Need the grid definitions
model_meshmask = model_data_cat["NEMO_ORCA05_FOCI_Test_mesh_mask"](
    chunks={"z": 23}
).to_dask()
model_meshmask = model_meshmask.squeeze()
model_meshmask = xr.decode_cf(model_meshmask)

In [17]:
display(model_dataset)
display(f"{model_dataset.nbytes / 1e9} GB")

<xarray.Dataset>
Dimensions:               (axis_nbounds: 2, deptht: 46, time_counter: 108, x: 722, y: 511)
Coordinates:
  * deptht                (deptht) float32 3.0467727 9.454049 ... 5875.141
    nav_lat               (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    nav_lon               (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    time_centered         (time_counter) datetime64[ns] dask.array<chunksize=(1,), meta=np.ndarray>
  * time_counter          (time_counter) datetime64[ns] 2011-01-16T12:00:00 ... 2019-12-16T12:00:00
Dimensions without coordinates: axis_nbounds, x, y
Data variables:
    deptht_bounds         (time_counter, deptht, axis_nbounds) float32 dask.array<chunksize=(12, 23, 2), meta=np.ndarray>
    votemper              (time_counter, deptht, y, x) float32 dask.array<chunksize=(1, 23, 511, 722), meta=np.ndarray>
    time_centered_bounds  (time_counter, axis_nbounds) datetime64[ns] dask.array<chunksize=(1, 2), meta=np.ndarray>
    time_counter_bounds   (time_counter, axis_nbounds) datetime64[ns] dask.array<chunksize=(1, 2), meta=np.ndarray>
    vosaline              (time_counter, deptht, y, x) float32 dask.array<chunksize=(1, 23, 511, 722), meta=np.ndarray>
    sosstsst              (time_counter, y, x) float32 dask.array<chunksize=(1, 511, 722), meta=np.ndarray>
    sosaline              (time_counter, y, x) float32 dask.array<chunksize=(1, 511, 722), meta=np.ndarray>
    sossheig              (time_counter, y, x) float32 dask.array<chunksize=(1, 511, 722), meta=np.ndarray>
    sowaflup              (time_counter, y, x) float32 dask.array<chunksize=(1, 511, 722), meta=np.ndarray>
    soshfldo              (time_counter, y, x) float32 dask.array<chunksize=(1, 511, 722), meta=np.ndarray>
    sohefldo              (time_counter, y, x) float32 dask.array<chunksize=(1, 511, 722), meta=np.ndarray>
    somxl010              (time_counter, y, x) float32 dask.array<chunksize=(1, 511, 722), meta=np.ndarray>
    somixhgt              (time_counter, y, x) float32 dask.array<chunksize=(1, 511, 722), meta=np.ndarray>
    sowindsp              (time_counter, y, x) float32 dask.array<chunksize=(1, 511, 722), meta=np.ndarray>
    sohefldp              (time_counter, y, x) float32 dask.array<chunksize=(1, 511, 722), meta=np.ndarray>
    sowafldp              (time_counter, y, x) float32 dask.array<chunksize=(1, 511, 722), meta=np.ndarray>
    sobowlin              (time_counter, y, x) float32 dask.array<chunksize=(1, 511, 722), meta=np.ndarray>
Attributes:
    name:         FOCI1.14-JH024_1m_20110101_20111231
    description:  ocean T grid variables
    title:        ocean T grid variables
    Conventions:  CF-1.5
    production:   An IPSL model
    timeStamp:    2019-Apr-17 18:02:10 CEST
    history:      Wed Apr 17 18:47:54 2019: ncks -7 -a -L 1 --cnk_dmn time,1 ...
    NCO:          4.4.8

'16.578822824 GB'

In [18]:
display(model_meshmask)
display(f"{model_meshmask.nbytes / 1e9} GB")

<xarray.Dataset>
Dimensions:       (x: 722, y: 511, z: 46)
Dimensions without coordinates: x, y, z
Data variables:
    nav_lon       (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    nav_lat       (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    nav_lev       (z) float32 dask.array<chunksize=(23,), meta=np.ndarray>
    time_counter  float64 dask.array<chunksize=(), meta=np.ndarray>
    tmask         (z, y, x) int8 dask.array<chunksize=(23, 511, 722), meta=np.ndarray>
    umask         (z, y, x) int8 dask.array<chunksize=(23, 511, 722), meta=np.ndarray>
    vmask         (z, y, x) int8 dask.array<chunksize=(23, 511, 722), meta=np.ndarray>
    fmask         (z, y, x) int8 dask.array<chunksize=(23, 511, 722), meta=np.ndarray>
    tmaskutil     (y, x) int8 dask.array<chunksize=(511, 722), meta=np.ndarray>
    umaskutil     (y, x) int8 dask.array<chunksize=(511, 722), meta=np.ndarray>
    vmaskutil     (y, x) int8 dask.array<chunksize=(511, 722), meta=np.ndarray>
    fmaskutil     (y, x) int8 dask.array<chunksize=(511, 722), meta=np.ndarray>
    glamt         (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    glamu         (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    glamv         (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    glamf         (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    gphit         (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    gphiu         (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    gphiv         (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    gphif         (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    e1t           (y, x) float64 dask.array<chunksize=(511, 722), meta=np.ndarray>
    e1u           (y, x) float64 dask.array<chunksize=(511, 722), meta=np.ndarray>
    e1v           (y, x) float64 dask.array<chunksize=(511, 722), meta=np.ndarray>
    e1f           (y, x) float64 dask.array<chunksize=(511, 722), meta=np.ndarray>
    e2t           (y, x) float64 dask.array<chunksize=(511, 722), meta=np.ndarray>
    e2u           (y, x) float64 dask.array<chunksize=(511, 722), meta=np.ndarray>
    e2v           (y, x) float64 dask.array<chunksize=(511, 722), meta=np.ndarray>
    e2f           (y, x) float64 dask.array<chunksize=(511, 722), meta=np.ndarray>
    ff            (y, x) float64 dask.array<chunksize=(511, 722), meta=np.ndarray>
    mbathy        (y, x) int16 dask.array<chunksize=(511, 722), meta=np.ndarray>
    misf          (y, x) int16 dask.array<chunksize=(511, 722), meta=np.ndarray>
    isfdraft      (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    e3t_0         (z, y, x) float64 dask.array<chunksize=(23, 511, 722), meta=np.ndarray>
    e3u_0         (z, y, x) float64 dask.array<chunksize=(23, 511, 722), meta=np.ndarray>
    e3v_0         (z, y, x) float64 dask.array<chunksize=(23, 511, 722), meta=np.ndarray>
    e3w_0         (z, y, x) float64 dask.array<chunksize=(23, 511, 722), meta=np.ndarray>
    gdept_0       (z, y, x) float32 dask.array<chunksize=(23, 511, 722), meta=np.ndarray>
    gdepu         (z, y, x) float32 dask.array<chunksize=(23, 511, 722), meta=np.ndarray>
    gdepv         (z, y, x) float32 dask.array<chunksize=(23, 511, 722), meta=np.ndarray>
    gdepw_0       (z, y, x) float32 dask.array<chunksize=(23, 511, 722), meta=np.ndarray>
    gdept_1d      (z) float64 dask.array<chunksize=(23,), meta=np.ndarray>
    gdepw_1d      (z) float64 dask.array<chunksize=(23,), meta=np.ndarray>
    e3t_1d        (z) float64 dask.array<chunksize=(23,), meta=np.ndarray>
    e3w_1d        (z) float64 dask.array<chunksize=(23,), meta=np.ndarray>

'0.928259736 GB'

In [19]:
# need compute / cast to numpy array here in order for datashade to work
# (see https://datashader.org/user_guide/Performance.html)
model_mean_sst = model_dataset.sosstsst.mean("time_counter").compute()
model_mean_sst = model_mean_sst.where(model_mean_sst != 0)

In [20]:
(
    model_mean_sst.hvplot.quadmesh(
        "nav_lon", "nav_lat",
        geo=True, datashade=True)
    * near_surface_obs.hvplot(
        "Longitude", "Latitude",
        geo=True, kind="points", color="red")
    * gf.land * gf.coastline
)

:DynamicMap   []
   :Overlay
      .RGB.I       :RGB   [nav_lon,nav_lat]   (R,G,B,A)
      .Points.I    :Points   [Longitude,Latitude]
      .Land.I      :Feature   [Longitude,Latitude]
      .Coastline.I :Feature   [Longitude,Latitude]

## Extract model data along ship track (surface positions)

In [21]:
xll2ij.get_ij?

Signature: xll2ij.get_ij(data, points, grid='F', xgcm=False, xarray_out=False)
Docstring:
Get i and j indeces of ORCA grid of specified lon and lat points.

Parameters
----------
data : xarray.DataSet
    Dataset of any variable(s) living on the specified grid if `xgcm=True`
    (i.e. DataArray has been loaded with load_orca_dataset) or DataSet of
    original `mesh_hgr.nc/meshmask.nc` if `xgcm=False` (default).
points : array
    Numpy array of shape=(n, 2). First column is latitudes, second column
    is longitudes.
    `array([[lat_1, lon_1], [lat_2, lon_2], ..., [lat_n, lon_n]])`
grid : str, optional
    Name of the grid (T, U, V, F). Default is `'F'` (which is the grid
    used for `xorca_brokenline`)
xgcm : bool, optional
    If `True`, dataset has to be compatible with xgcm. Default is `False`.
xarray_out : bool, optional
    If `True` output will be of type `xarray.DataArray`. Default is
    `False`.

Returns
-------
X : array or tuple
    `X` is a numpy array of shape=(n, 2), 

In [22]:
positions = list(zip(
    near_surface_obs["Latitude"],
    near_surface_obs["Longitude"],
))

depths = near_surface_obs["Depth water"].to_xarray()
depths

times = near_surface_obs["Date/Time"].to_xarray()

lat_ind, lon_ind = xll2ij.get_ij(
    model_meshmask, positions, 't', xgcm=False, xarray_out=True)
lat_ind = lat_ind.rename({"location": "Event"})
lon_ind = lon_ind.rename({"location": "Event"})

In [23]:
model_dataset["deptht"] = model_dataset["deptht"].compute()
model_dataset["time_counter"] = model_dataset["time_counter"].compute()
model_dataset["y"] = np.arange(model_dataset.dims["y"])
model_dataset["x"] = np.arange(model_dataset.dims["x"])

In [24]:
# select
ship_track_data = model_dataset.isel(y=lat_ind, x=lon_ind)
ship_track_data = ship_track_data.sel(deptht=depths, method="nearest")
ship_track_data = ship_track_data.sel(time_counter=times, method="nearest")

# mask
ship_track_data = ship_track_data.where(ship_track_data.votemper != 0)

display(ship_track_data)

<xarray.Dataset>
Dimensions:               (Event: 606, axis_nbounds: 2)
Coordinates:
    deptht                (Event) float32 3.0467727 3.0467727 ... 3.0467727
    nav_lat               (Event) float32 dask.array<chunksize=(606,), meta=np.ndarray>
    nav_lon               (Event) float32 dask.array<chunksize=(606,), meta=np.ndarray>
    time_centered         (Event) datetime64[ns] dask.array<chunksize=(36,), meta=np.ndarray>
    time_counter          (Event) datetime64[ns] 2014-04-16 ... 2012-11-16
    y                     (Event) int64 285 285 285 279 279 ... 218 218 218 219
    x                     (Event) int64 526 526 526 528 528 ... 422 423 423 423
  * Event                 (Event) object 'M106_322-2' ... 'M90_1711-1'
Dimensions without coordinates: axis_nbounds
Data variables:
    deptht_bounds         (Event, axis_nbounds) float32 dask.array<chunksize=(606, 2), meta=np.ndarray>
    votemper              (Event) float32 dask.array<chunksize=(606,), meta=np.ndarray>
    time_centered_bounds  (Event, axis_nbounds) datetime64[ns] dask.array<chunksize=(36, 2), meta=np.ndarray>
    time_counter_bounds   (Event, axis_nbounds) datetime64[ns] dask.array<chunksize=(36, 2), meta=np.ndarray>
    vosaline              (Event) float32 dask.array<chunksize=(606,), meta=np.ndarray>
    sosstsst              (Event) float32 dask.array<chunksize=(606,), meta=np.ndarray>
    sosaline              (Event) float32 dask.array<chunksize=(606,), meta=np.ndarray>
    sossheig              (Event) float32 dask.array<chunksize=(606,), meta=np.ndarray>
    sowaflup              (Event) float32 dask.array<chunksize=(606,), meta=np.ndarray>
    soshfldo              (Event) float32 dask.array<chunksize=(606,), meta=np.ndarray>
    sohefldo              (Event) float32 dask.array<chunksize=(606,), meta=np.ndarray>
    somxl010              (Event) float32 dask.array<chunksize=(606,), meta=np.ndarray>
    somixhgt              (Event) float32 dask.array<chunksize=(606,), meta=np.ndarray>
    sowindsp              (Event) float32 dask.array<chunksize=(606,), meta=np.ndarray>
    sohefldp              (Event) float32 dask.array<chunksize=(606,), meta=np.ndarray>
    sowafldp              (Event) float32 dask.array<chunksize=(606,), meta=np.ndarray>
    sobowlin              (Event) float32 dask.array<chunksize=(606,), meta=np.ndarray>
Attributes:
    name:         FOCI1.14-JH024_1m_20110101_20111231
    description:  ocean T grid variables
    title:        ocean T grid variables
    Conventions:  CF-1.5
    production:   An IPSL model
    timeStamp:    2019-Apr-17 18:02:10 CEST
    history:      Wed Apr 17 18:47:54 2019: ncks -7 -a -L 1 --cnk_dmn time,1 ...
    NCO:          4.4.8

In [25]:
%%time

ship_track_data = ship_track_data.compute()

CPU times: user 1.73 s, sys: 198 ms, total: 1.93 s
Wall time: 3.67 s


In [26]:
(
    ship_track_data.to_dataframe().hvplot.scatter("votemper", "vosaline", label="surface data, model")
    * near_surface_obs.hvplot.scatter("Temp", "Sal", alpha=0.8, label="surface data, obs")
)

:Overlay
   .Scatter.Surface_data_comma_model :Scatter   [votemper]   (vosaline)
   .Scatter.Surface_data_comma_obs   :Scatter   [Temp]   (Sal)

## Extract model data along ship track (all depths)

In [27]:
positions = list(zip(
    obs_df["Latitude"],
    obs_df["Longitude"],
))

depths = obs_df["Depth water"].to_xarray()
depths

times = obs_df["Date/Time"].to_xarray()

lat_ind, lon_ind = xll2ij.get_ij(
    model_meshmask, positions, 't', xgcm=False, xarray_out=True)
lat_ind = lat_ind.rename({"location": "index"})
lon_ind = lon_ind.rename({"location": "index"})

In [28]:
len(lon_ind)

798444

In [30]:
%%time

# OPTIMIZE: Here, we have ~ 800_000 positions that we select.
#           If we don't fully load the dataset before computing,
#           we're left with an enormous Dask graph.
model_dataset = model_dataset.compute()

# select
ship_track_data = model_dataset.sel(
    y=lat_ind, x=lon_ind, deptht=depths, time_counter=times, method="nearest"
)

# mask
ship_track_data = ship_track_data.where(ship_track_data.votemper != 0)

display(ship_track_data)

<xarray.Dataset>
Dimensions:               (axis_nbounds: 2, index: 798444)
Coordinates:
    deptht                (index) float32 322.0169 322.0169 ... 134.28227
    nav_lat               (index) float32 49.277622 49.277622 ... -22.867542
    nav_lon               (index) float32 -11.130844 -11.130844 ... 13.75 13.75
    time_centered         (index) datetime64[ns] 2011-06-16 ... 2015-11-16
    time_counter          (index) datetime64[ns] 2011-06-16 ... 2015-11-16
    y                     (index) int64 362 362 362 362 362 ... 202 202 202 202
    x                     (index) int64 551 551 551 551 551 ... 602 602 602 602
  * index                 (index) int64 0 1 2 3 ... 798440 798441 798442 798443
Dimensions without coordinates: axis_nbounds
Data variables:
    deptht_bounds         (index, axis_nbounds) float32 nan nan ... 146.73515
    votemper              (index) float32 nan nan nan ... 14.039388 14.039388
    time_centered_bounds  (index, axis_nbounds) datetime64[ns] NaT ... 2015-12-01
    time_counter_bounds   (index, axis_nbounds) datetime64[ns] NaT ... 2015-12-01
    vosaline              (index) float32 nan nan nan ... 35.060234 35.060234
    sosstsst              (index) float32 nan nan nan ... 21.54325 21.54325
    sosaline              (index) float32 nan nan nan ... 35.391556 35.391556
    sossheig              (index) float32 nan nan nan ... 0.70417184 0.70417184
    sowaflup              (index) float32 nan nan ... 2.836045e-05 2.836045e-05
    soshfldo              (index) float32 nan nan nan ... 315.6222 315.6222
    sohefldo              (index) float32 nan nan nan ... 171.82306 171.82306
    somxl010              (index) float32 nan nan nan ... 13.594714 13.594714
    somixhgt              (index) float32 nan nan nan ... 15.194402 15.194402
    sowindsp              (index) float32 nan nan nan ... 4.859168 4.859168
    sohefldp              (index) float32 nan nan nan nan ... nan nan nan nan
    sowafldp              (index) float32 nan nan nan nan ... nan nan nan nan
    sobowlin              (index) float32 nan nan nan ... 20.04454 20.04454
Attributes:
    name:         FOCI1.14-JH024_1m_20110101_20111231
    description:  ocean T grid variables
    title:        ocean T grid variables
    Conventions:  CF-1.5
    production:   An IPSL model
    timeStamp:    2019-Apr-17 18:02:10 CEST
    history:      Wed Apr 17 18:47:54 2019: ncks -7 -a -L 1 --cnk_dmn time,1 ...
    NCO:          4.4.8

CPU times: user 43.6 s, sys: 42.1 s, total: 1min 25s
Wall time: 1min 40s


In [31]:
%%time

all_depths_plot = (
    decimate(
        ship_track_data.to_dataframe().hvplot.scatter(
            "votemper", "vosaline", alpha=0.4, label="surface data, model"
        )
    )
    * decimate(
        obs_df.hvplot.scatter(
            "Tpot", "Sal", alpha=0.4, label="surface data, obs"
        )
    )
)

CPU times: user 488 ms, sys: 487 ms, total: 975 ms
Wall time: 882 ms


In [32]:
all_depths_plot

:DynamicMap   []
   :Overlay
      .Scatter.Surface_data_comma_model :Scatter   [votemper]   (vosaline)
      .Scatter.Surface_data_comma_obs   :Scatter   [Tpot]   (Sal)